# Benchmark

We use a list of public datasets to benchmark all the algorithms in StreamAD. Thanks!

1. AIOPS_KPI, [AIOps Challenge public dataset for KPI anomaly detection](https://github.com/NetManAIOps/KPI-Anomaly-Detection)
2. AWSCloudwatch, [AWS server metrics](https://github.com/numenta/NAB/tree/master/data/realAWSCloudwatch)
3. GAIA, [GAIA](https://github.com/CloudWise-OpenSource/GAIA-DataSet/tree/main/Companion_Data)

In [1]:

import pandas as pd
import numpy as np
from tqdm import tqdm
from time import perf_counter
from streamad.util import StreamGenerator, CustomDS
from streamad.evaluate import NumentaAwareMetircs, PointAwareMetircs, SeriesAwareMetircs
from dataset import prepare_ds, read_ds
from streamad.model import KNNDetector, xStreamDetector, SpotDetector, RandomDetector, RShashDetector, SRDetector, RrcfDetector, HSTreeDetector, ZScoreDetector, LodaDetector, OCSVMDetector, MadDetector, SArimaDetector,ZSpotDetector


We download the dataset, unzip it, and reconstruct its structure with **prepare_ds()** and load the dataset with **read_ds()**

By now, **ds_name** and **file_name** are represented by

```python

DS = {
    "AIOPS_KPI": ["preliminary_train", "finals_train", "finals_ground_truth"],
    "AWSCloudwatch": [],
    "GAIA": [
        "changepoint_data",
        "concept_drift_data",
        "linear_data",
        "low_signal-to-noise_ratio_data",
        "partially_stationary_data",
        "periodic_data",
        "staircase_data",
    ],
```



In [46]:
path = './streamad-benchmark-dataset'
ds_name = 'MICRO'
prepare_ds(ds_name=ds_name,path=path)

Dataset AWSCloudwatch already exists


In [47]:
dfs = read_ds(ds_name=ds_name,ds_file="periodic_data")

In [48]:
benchmark_items = [
    "Detector",
    "Dataset",
    "Key",
    "Size(#)",
    "Time(s)",
    "Point_Precision",
    "Point_Recall",
    "Point_Fbeta",
    "Series_Precision",
    "Series_Recall",
    "Series_Fbeta",
    "Numenta_Precision",
    "Numenta_Recall",
    "Numenta_Fbeta",
]
benchmark_df = pd.DataFrame(columns=benchmark_items)

In [35]:
models = {
# KNNDetector: dict(),
# xStreamDetector: dict(),
SpotDetector: dict(back_mean_len=5, global_memory=True, window_len=20),
# ZSpotDetector: dict(back_mean_len=5, z=3, window_len=20),
# RandomDetector: dict(),
# ZScoreDetector: dict(window_len=400),
}

In [52]:
threshold = 0.7
for key, (df, label) in dfs.items():

    ds = CustomDS(df, label)
    stream = StreamGenerator(ds.data)

    for model_class, model_param in models.items():
        model = model_class(**model_param)
        scores = []
        start_time = perf_counter()
        for x in tqdm(stream.iter_item(), total=len(ds.data)):
            score = model.fit_score(x)
            if score is not None:
                score = 1 if score >= threshold else score
            
            scores.append(score)

        time = perf_counter() - start_time

        benchmark_values = [model.__class__.__name__, ds_name, key, len(ds.data), time]

        label = ds.label
        for metric in [
            PointAwareMetircs(),
            SeriesAwareMetircs(),
            NumentaAwareMetircs(),
        ]:
            # scores = np.nan_to_num(np.array(scores, dtype=float), nan=0)
            benchmark_values.extend(list(metric.evaluate(label, scores)))

        benchmark_df.loc[len(benchmark_df)] = benchmark_values

        from streamad.util import plot
        data, label, date, features = ds.data, ds.label, ds.date, ds.features
        idx=0
        gap=50000
        data = data[idx:idx+gap]
        scores=scores[idx:idx+gap]
        date=date[idx:idx+gap]
        label=label[idx:idx+gap]
        fig = plot(data=data,scores=scores,date=date,features=features,label=label)
        fig.show()
        fig.write_image(f"./image/{model.__class__.__name__}_{key}.png")
    # break
    


100%|██████████| 4032/4032 [00:06<00:00, 670.31it/s] 


100%|██████████| 4032/4032 [00:00<00:00, 4088.22it/s]


100%|██████████| 4032/4032 [00:03<00:00, 1176.86it/s]


100%|██████████| 4032/4032 [00:05<00:00, 784.41it/s] 


100%|██████████| 4032/4032 [00:03<00:00, 1021.17it/s]


...

100%|██████████| 1243/1243 [00:00<00:00, 2699.35it/s]


100%|██████████| 4032/4032 [00:03<00:00, 1311.18it/s]


100%|██████████| 4032/4032 [00:03<00:00, 1258.14it/s]


100%|██████████| 4621/4621 [00:04<00:00, 1060.32it/s]


100%|██████████| 4032/4032 [00:02<00:00, 1451.62it/s]


In [13]:
benchmark_df

Detector Dataset                                                Key  \
0   ZSpotDetector    GAIA  low_signal-to-noise_ratio_data_16_from2019-11-...   
1   ZSpotDetector    GAIA  low_signal-to-noise_ratio_data_21_from2019-11-...   
2   ZSpotDetector    GAIA  low_signal-to-noise_ratio_data_7_from2019-11-1...   
3   ZSpotDetector    GAIA  low_signal-to-noise_ratio_data_25_from2019-01-...   
4   ZSpotDetector    GAIA  low_signal-to-noise_ratio_data_47_from2019-11-...   
5   ZSpotDetector    GAIA  low_signal-to-noise_ratio_data_11_from2019-11-...   
6   ZSpotDetector    GAIA  low_signal-to-noise_ratio_data_19_from2019-01-...   
7   ZSpotDetector    GAIA  low_signal-to-noise_ratio_data_1_from2019-08-1...   
8   ZSpotDetector    GAIA  low_signal-to-noise_ratio_data_5_from2019-11-1...   
9   ZSpotDetector    GAIA  low_signal-to-noise_ratio_data_37_from2019-11-...   
10  ZSpotDetector    GAIA  low_signal-to-noise_ratio_data_22_from2019-11-...   
11  ZSpotDetector    GAIA  low_signal-to-noise_ratio_data_12_from2019-11-...   
12  ZSpotDetector    GAIA  low_signal-to-noise_ratio_data_38_from2019-11-...   
13  ZSpotDetector    GAIA  low_signal-to-noise_ratio_data_32_from2019-11-...   
14  ZSpotDetector    GAIA  low_signal-to-noise_ratio_data_10_from2019-12-...   
15  ZSpotDetector    GAIA  low_signal-to-noise_ratio_data_3_from2019-11-1...   
16  ZSpotDetector    GAIA  low_signal-to-noise_ratio_data_14_from2019-11-...   
17  ZSpotDetector    GAIA  low_signal-to-noise_ratio_data_35_from2018-12-...   
18  ZSpotDetector    GAIA  low_signal-to-noise_ratio_data_42_from2019-11-...   
19  ZSpotDetector    GAIA  low_signal-to-noise_ratio_data_30_from2018-12-...   
20  ZSpotDetector    GAIA  low_signal-to-noise_ratio_data_17_from2019-11-...   
21  ZSpotDetector    GAIA  low_signal-to-noise_ratio_data_41_from2019-11-...   
22  ZSpotDetector    GAIA  low_signal-to-noise_ratio_data_46_from2018-12-...   
23  ZSpotDetector    GAIA  low_signal-to-noise_ratio_data_49_from2019-08-...   
24  ZSpotDetector    GAIA  low_signal-to-noise_ratio_data_34_from2019-11-...   
25  ZSpotDetector    GAIA  low_signal-to-noise_ratio_data_24_from2019-11-...   
26  ZSpotDetector    GAIA  low_signal-to-noise_ratio_data_0_from2019-11-1...   
27  ZSpotDetector    GAIA  low_signal-to-noise_ratio_data_33_from2019-11-...   
28  ZSpotDetector    GAIA  low_signal-to-noise_ratio_data_44_from2019-09-...   
29  ZSpotDetector    GAIA  low_signal-to-noise_ratio_data_20_from2019-11-...   
30  ZSpotDetector    GAIA  low_signal-to-noise_ratio_data_18_from2018-12-...   
31  ZSpotDetector    GAIA  low_signal-to-noise_ratio_data_28_from2019-01-...   
32  ZSpotDetector    GAIA  low_signal-to-noise_ratio_data_6_from2019-09-1...   
33  ZSpotDetector    GAIA  low_signal-to-noise_ratio_data_4_from2019-11-1...   
34  ZSpotDetector    GAIA  low_signal-to-noise_ratio_data_39_from2020-11-...   
35  ZSpotDetector    GAIA  low_signal-to-noise_ratio_data_36_from2019-11-...   
36  ZSpotDetector    GAIA  low_signal-to-noise_ratio_data_13_from2019-11-...   
37  ZSpotDetector    GAIA  low_signal-to-noise_ratio_data_31_from2019-12-...   
38  ZSpotDetector    GAIA  low_signal-to-noise_ratio_data_23_from2019-11-...   
39  ZSpotDetector    GAIA  low_signal-to-noise_ratio_data_45_from2019-11-...   
40  ZSpotDetector    GAIA  low_signal-to-noise_ratio_data_27_from2019-12-...   
41  ZSpotDetector    GAIA  low_signal-to-noise_ratio_data_2_from2019-11-1...   
42  ZSpotDetector    GAIA  low_signal-to-noise_ratio_data_15_from2019-11-...   
43  ZSpotDetector    GAIA  low_signal-to-noise_ratio_data_26_from2019-11-...   
44  ZSpotDetector    GAIA  low_signal-to-noise_ratio_data_40_from2019-11-...   
45  ZSpotDetector    GAIA  low_signal-to-noise_ratio_data_8_from2019-11-1...   
46  ZSpotDetector    GAIA  low_signal-to-noise_ratio_data_9_from2019-11-1...   
47  ZSpotDetector    GAIA  low_signal-to-noise_ratio_data_43_from2019-11-...   
48  ZSpotDetector    GAIA  low_signal-to-noise_ratio_data_29_from2019-11-...   
49  ZSpot

In [10]:
benchmark_df.to_csv('./benchamark_results.csv', index=False)


In [51]:
# We can check the results and plot the figures, not for necessary.
from streamad.util import plot
data, label, date, features = ds.data, ds.label, ds.date, ds.features
idx=0
gap=50000
data = data[idx:idx+gap]
scores=scores[idx:idx+gap]
date=date[idx:idx+gap]
label=label[idx:idx+gap]
plot(data=data,scores=scores,date=date,features=features,label=label)

## Plot the benchmark results into a table

In [15]:
import plotly.graph_objects as go
import pandas as pd
import numpy as np
benchmark_df = pd.read_csv("./benchamark_results.csv")
# fig = go.Figure(
#     data=[
#         go.Table(
#             header=dict(values=list(benchmark_df.columns)),
#             cells=dict(
#                 values=[
#                     benchmark_df[i].round(decimals=5)
#                     if benchmark_df[i].dtype is np.dtype("float") or benchmark_df[i].dtype is np.dtype("int")
#                     else benchmark_df[i]
#                     for i in benchmark_df.columns.tolist()
#                 ],
#                 format=[""]*3 + [".3f"] * (len(benchmark_df.columns)-3),
#                 fill_color='white',
#                 line_color='lightgrey'
#             ),
#         ),
        
#     ],
# )
# fig.update_layout(margin=dict(l=0, r=0, t=0, b=0))
# fig.write_image("benchmark_results.svg")
# fig


Write benchmark results into a table file.

In [16]:
benchmark_df = benchmark_df.applymap(lambda x: round(x,3) if isinstance(x,(int,float)) else x)
content = benchmark_df.to_markdown(index=False)

with open('../docs/source/benchmark.md','w') as f:
    f.write('# Benchmark \n' + content)

In [20]:
pd.set_option('display.max_rows', 1000)
benchmark_df.to_clipboard(index=False)

In [21]:
benchmark_df

Detector Dataset                                             Key  \
0   SpotDetector    GAIA   linear_data_4_from2018-12-19to2019-01-31_8313   
1   SpotDetector    GAIA  linear_data_42_from2018-12-19to2019-01-31_8153   
2   SpotDetector    GAIA   linear_data_7_from2018-12-19to2019-01-31_8300   
3   SpotDetector    GAIA  linear_data_11_from2018-12-19to2019-01-31_8164   
4   SpotDetector    GAIA  linear_data_32_from2018-12-19to2019-01-31_8151   
5   SpotDetector    GAIA  linear_data_25_from2018-12-19to2019-01-31_8412   
6   SpotDetector    GAIA   linear_data_4_from2018-12-19to2019-01-31_8313   
7   SpotDetector    GAIA  linear_data_42_from2018-12-19to2019-01-31_8153   
8   SpotDetector    GAIA   linear_data_7_from2018-12-19to2019-01-31_8300   
9   SpotDetector    GAIA  linear_data_11_from2018-12-19to2019-01-31_8164   
10  SpotDetector    GAIA  linear_data_32_from2018-12-19to2019-01-31_8151   
11  SpotDetector    GAIA  linear_data_25_from2018-12-19to2019-01-31_8412   
12  SpotDetector    GAIA   linear_data_8_from2018-12-19to2019-01-31_8329   
13  SpotDetector    GAIA  linear_data_57_from2018-12-19to2019-01-31_8268   
14  SpotDetector    GAIA  linear_data_41_from2018-12-19to2019-01-31_8386   
15  SpotDetector    GAIA  linear_data_29_from2018-12-19to2019-01-31_8410   
16  SpotDetector    GAIA  linear_data_54_from2018-12-19to2019-01-31_8319   
17  SpotDetector    GAIA  linear_data_12_from2018-12-19to2019-01-31_8372   
18  SpotDetector    GAIA  linear_data_26_from2018-12-19to2019-01-31_8348   
19  SpotDetector    GAIA  linear_data_31_from2018-12-19to2019-01-31_8192   
20  SpotDetector    GAIA  linear_data_58_from2018-12-19to2019-01-31_8334   
21  SpotDetector    GAIA  linear_data_30_from2018-12-19to2019-01-31_8376   
22  SpotDetector    GAIA  linear_data_20_from2018-12-19to2019-01-31_8210   
23  SpotDetector    GAIA  linear_data_43_from2019-11-16to2019-12-16_2584   
24  SpotDetector    GAIA  linear_data_48_from2018-12-19to2019-01-31_8425   
25  SpotDetector    GAIA  linear_data_51_from2018-12-19to2019-01-31_8286   
26  SpotDetector    GAIA   linear_data_2_from2018-12-19to2019-01-31_8304   
27  SpotDetector    GAIA  linear_data_17_from2018-12-19to2019-01-31_8159   
28  SpotDetector    GAIA  linear_data_13_from2019-11-16to2019-12-16_1646   
29  SpotDetector    GAIA  linear_data_18_from2018-12-19to2019-01-31_8167   
30  SpotDetector    GAIA  linear_data_34_from2018-12-19to2019-01-31_8385   
31  SpotDetector    GAIA  linear_data_47_from2019-01-01to2019-01-31_7946   
32  SpotDetector    GAIA  linear_data_37_from2018-12-19to2019-01-31_8378   
33  SpotDetector    GAIA   linear_data_1_from2019-01-01to2019-01-31_7861   
34  SpotDetector    GAIA  linear_data_23_from2018-12-19to2019-01-31_8199   
35  SpotDetector    GAIA  linear_data_52_from2019-01-01to2019-01-31_8145   
36  SpotDetector    GAIA  linear_data_44_from2018-12-19to2019-01-31_8396   
37  SpotDetector    GAIA  linear_data_38_from2018-12-19to2019-01-31_8224   
38  SpotDetector    GAIA  linear_data_14_from2018-12-19to2019-01-31_8213   
39  SpotDetector    GAIA  linear_data_33_from2018-12-19to2019-01-31_8232   
40  SpotDetector    GAIA   linear_data_9_from2018-12-19to2019-01-31_8315   
41  SpotDetector    GAIA  linear_data_56_from2019-01-01to2019-01-31_8146   
42  SpotDetector    GAIA   linear_data_6_from2018-12-19to2019-01-31_8263   
43  SpotDetector    GAIA  linear_data_24_from2018-12-19to2019-01-31_8360   
44  SpotDetector    GAIA  linear_data_10_from2018-12-19to2019-01-31_8158   
45  SpotDetector    GAIA  linear_data_40_from2018-12-19to2019-01-31_8219   
46  SpotDetector    GAIA  linear_data_28_from2018-12-19to2019-01-31_8163   
47  SpotDetector    GAIA  linear_data_55_from2018-12-19to2019-01-31_8332   
48  SpotDetector    GAIA   linear_data_5_from2018-12-19to2019-01-31_8277   
49  SpotDetector    GAIA  linear_data_27_from2018-12-19to2019-01-31_8177   
50  SpotDetector    GAIA  linear_data_21_from2018-12-19to2019-01-31_8172   
51  SpotDetector    GAIA   linear_data_3_from2018-12-19t

In [ ]:
path = './streamad-benchmark-dataset'
ds_name = 'AWSCloudwatch'
prepare_ds(ds_name=ds_name,path=path)


In [ ]:
from sklearn.metrics import recall_score

true = [0,0,0,0,0,0]
predict = [0,1,0,0,0,0]

recall_score(true,predict, zero_division=1)